In [248]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [280]:
import pandas as pd
import re
import json
import h2o

from datetime import datetime
from functools import lru_cache

from utils import get_data, Config

from tree import make_tree

In [250]:
def clean_url(url):
    return re.sub(r"browser_id=(\d+)", "browser_id=1", url)

def make_clickable(url):
    # Clickable links for debugging; set browser_id=2 (unknown) to not count them in our real data collection
    url = clean_url(url)
    return f'<a href="{url}" target="_blank">{url}</a>'

In [251]:
@lru_cache(maxsize=None)
def id_to_browser(id):
    return " ".join(df.loc[df["browser_id"] == id].iloc[0][["name", "os", "version", "automation_mode", "headless_mode"]].to_list())

## Load Data + Preprocessing

In [252]:
# Load all data
initial_data = """
SELECT "Result".*, 
"Response".raw_header, "Response".status_code, "Response".label, "Response".resp_type,
"Browser".name, "Browser".version, "Browser".headless_mode, "Browser".os, "Browser".automation_mode, "Browser".add_info
FROM "Result"
JOIN "Response" ON "Result".response_id = "Response".id JOIN "Browser" ON "Result".browser_id = "Browser".id
WHERE "Browser".name != 'Unknown';
"""
df = get_data(Config(), initial_data)

Connecting to the PostgreSQL database...
Connection successful


In [253]:
# Extra columns
df["outcome_str"] = df["outcome_value"].fillna("None").astype(str)

# Unify outcomes that are the same
# Firefox: {'error': 'object "TypeError: NetworkError when attempting to fetch resource."', 'headers': ''} Chromium: {'error': 'object "TypeError: Failed to fetch"', 'headers': ''}
# Safari: {'error': 'object "TypeError: Load failed"', 'headers': ''}
df["outcome_str"] = df["outcome_str"].replace("{'error': 'object \"TypeError: NetworkError when attempting to fetch resource.\"', 'headers': ''}", "{'error': 'object \"TypeError: Failed to fetch\"', 'headers': ''}")
df["outcome_str"] = df["outcome_str"].replace("{'error': 'object \"TypeError: Load failed\"', 'headers': ''}", "{'error': 'object \"TypeError: Failed to fetch\"', 'headers': ''}")

# For document referrer we do not want to know the exact resp_id and count
# Maybe we even only want to know whether it is a origin or the full URl?
df['outcome_str'] = df['outcome_str'].replace(r'resp_id=\d+', 'resp_id=<resp_id>', regex=True)
df['outcome_str'] = df['outcome_str'].replace(r'count=\d+', 'count=<count>', regex=True)

df["clean_url"] = df["full_url"].apply(clean_url)

df["browser"] = df["browser_id"].apply(id_to_browser)
df["org_origin"] = df["org_scheme"] + "://" + df["org_host"]
df["resp_origin"] = df["resp_scheme"] + "://" + df["resp_host"]

In [254]:
df["outcome_str"].unique()

array(['window.originAgentCluster: true',
       'document.referrer: https://headers.websec.saarland/',
       "{'response.redirected': False}",
       "{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'load', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'load'}, 'window.crossOriginIsolated': False}",
       "{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'error', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'error'}, 'window.crossOriginIsolated': False}",
       "{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'load', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'error'}, 'window.crossOriginIsolated': False}",
       'No performance entry', "{'requestStart != 0': True}",
       'document.referrer: ',
       "{'error': 'null', 'headers': 'access-control-allow-origin,content-length,date,server,test,'}",
       "{'error': 'null', 'headers': 'content-length,'}",
       '{\'error\': \'object "TypeError: Failed to fetch"\', \

## Overview

In [255]:
display(df.head(2))
display(df.describe())
display(df.columns)

id   outcome_type                                      outcome_value  \
0  485827  <class 'str'>                    window.originAgentCluster: true   
1  485870  <class 'str'>  document.referrer: https://headers.websec.saar...   

         test_name  test_status test_message test_stack org_scheme  \
0  oac_window.open            0         None       None       http   
1  referrer_iframe            0         None       None      https   

                      org_host resp_scheme  ...   version headless_mode  \
0  sub.headers.websec.saarland       https  ...  1.60.116          real   
1  sub.headers.websec.saarland        http  ...  1.60.116          real   

           os  automation_mode  add_info  \
0  Android 11           intent             
1  Android 11           intent             

                                         outcome_str  \
0                    window.originAgentCluster: true   
1  document.referrer: https://headers.websec.saar...   

                                           clean_url  \
0  http://sub.headers.websec.saarland/_hp/tests/o...   
1  https://sub.headers.websec.saarland/_hp/tests/...   

                                 browser                           org_origin  \
0  brave Android 11 1.60.116 intent real   http://sub.headers.websec.saarland   
1  brave Android 11 1.60.116 intent real  https://sub.headers.websec.saarland   

                      resp_origin  
0    https://headers.webappsec.eu  
1  http://headers.websec.saarland  

[2 rows x 34 columns]

id    test_status     browser_id  testcase_id  \
count  434904.000000  434904.000000  434904.000000     434904.0   
mean   436376.929633       0.022971      19.890394          1.0   
min    192957.000000       0.000000       3.000000          1.0   
25%    301994.750000       0.000000      15.000000          1.0   
50%    435668.500000       0.000000      20.000000          1.0   
75%    572949.250000       0.000000      27.000000          1.0   
max    681675.000000       2.000000      32.000000          1.0   
std    149091.783931       0.213105       7.959466          0.0   

         response_id                     created_at  \
count  434904.000000                         434904   
mean       80.947998  2023-12-25 14:56:53.569531392   
min         4.000000     2023-12-20 09:58:40.566554   
25%        24.000000  2023-12-20 11:12:33.172862208   
50%        49.000000  2023-12-21 07:51:14.472970496   
75%       155.000000  2024-01-03 22:32:49.818516224   
max       218.000000     2024-01-05 13:34:56.729700   
std        67.397635                            NaN   

                          updated_at    status_code  
count                         434904  434904.000000  
mean   2023-12-25 14:56:53.569533440     216.277868  
min       2023-12-20 09:58:40.566558     200.000000  
25%    2023-12-20 11:12:33.172863232     200.000000  
50%    2023-12-21 07:51:14.472971520     200.000000  
75%    2024-01-03 22:32:49.818517248     200.000000  
max       2024-01-05 13:34:56.729708     302.000000  
std                              NaN      37.354742

Index(['id', 'outcome_type', 'outcome_value', 'test_name', 'test_status',
       'test_message', 'test_stack', 'org_scheme', 'org_host', 'resp_scheme',
       'resp_host', 'relation_info', 'browser_id', 'testcase_id',
       'response_id', 'status', 'full_url', 'created_at', 'updated_at',
       'raw_header', 'status_code', 'label', 'resp_type', 'name', 'version',
       'headless_mode', 'os', 'automation_mode', 'add_info', 'outcome_str',
       'clean_url', 'browser', 'org_origin', 'resp_origin'],
      dtype='object')

In [256]:
# Collected results per browser
df.groupby(["automation_mode", "browser_id", "name", "version", "os", "headless_mode"])["id"].count().sort_values(ascending=False).to_frame()

id
automation_mode browser_id name         version                   os           headless_mode       
intent          27         brave        1.61 (23.12.18.22)        iPadOS 17.2  real           35845
                31         operagx      2.2.2                     iPadOS 17.2  real           29503
                29         firefox      121.0 (36782)             iPadOS 17.2  real           26391
                32         edge         120.0.2210.116            iPadOS 17.2  real           25083
                26         chrome       120.0.6099.119            iPadOS 17.2  real           24939
                3          brave        1.60.116                  Android 11   real           21594
selenium        19         firefox      119                       Ubuntu 22.04 xvfb           20912
                20         edge         119                       Ubuntu 22.04 xvfb           20912
                17         brave        1.60.114 (119.0.6045.124) Ubuntu 22.04 headless-new   20912
intent          5          opera        78.4.4143.75735           Android 11   real           20912
selenium        13         chrome       119                       Ubuntu 22.04 headless-new   20912
                14         firefox      119                       Ubuntu 22.04 headless       20912
                16         brave        1.59.120 (118.0.5993.88)  Ubuntu 22.04 headless-new   20912
                15         edge         119                       Ubuntu 22.04 headless-new   20912
                21         brave        1.59.120 (118.0.5993.88)  Ubuntu 22.04 xvfb           20912
                22         brave        1.60.114 (119.0.6045.124) Ubuntu 22.04 xvfb           20912
                18         chrome       119                       Ubuntu 22.04 xvfb           20912
intent          12         chrome       120.0.6099.44             Android 11   real           20853
                23         firefox_beta 122.0b1                   Android 11   real           20059
                28         opera        4.4.1 (0)                 iPadOS 17.2  real             256
                4          ucmobile     13.3.8.1305               Android 11   real             253
                30         safari       17                        iPadOS 17.2  real              96

In [257]:
# Timeouts
display(df.groupby(["automation_mode", "browser_id", "name", "version", "os", "headless_mode"])["test_status"].value_counts().to_frame())

display(df.loc[df["test_status"] == 2].head(3))

count
automation_mode browser_id name         version                   os           headless_mode test_status       
intent          3          brave        1.60.116                  Android 11   real          0            21594
                4          ucmobile     13.3.8.1305               Android 11   real          0              206
                                                                                             2               47
                5          opera        78.4.4143.75735           Android 11   real          0            20912
                12         chrome       120.0.6099.44             Android 11   real          0            20853
                23         firefox_beta 122.0b1                   Android 11   real          0            19973
                                                                                             2               86
                26         chrome       120.0.6099.119            iPadOS 17.2  real          0            24939
                27         brave        1.61 (23.12.18.22)        iPadOS 17.2  real          0            31001
                                                                                             2             4844
                28         opera        4.4.1 (0)                 iPadOS 17.2  real          0              256
                29         firefox      121.0 (36782)             iPadOS 17.2  real          0            26391
                30         safari       17                        iPadOS 17.2  real          0               96
                31         operagx      2.2.2                     iPadOS 17.2  real          0            29503
                32         edge         120.0.2210.116            iPadOS 17.2  real          0            25083
selenium        13         chrome       119                       Ubuntu 22.04 headless-new  0            20912
                14         firefox      119                       Ubuntu 22.04 headless      0            20911
                                                                                             2                1
                15         edge         119                       Ubuntu 22.04 headless-new  0            20910
                                                                                             2                2
                16         brave        1.59.120 (118.0.5993.88)  Ubuntu 22.04 headless-new  0            20912
                17         brave        1.60.114 (119.0.6045.124) Ubuntu 22.04 headless-new  0            20912
                18         chrome       119                       Ubuntu 22.04 xvfb          0            20912
                19         firefox      119                       Ubuntu 22.04 xvfb          0            20907
                                                                                             2                5
                20         edge         119                       Ubuntu 22.04 xvfb          0            20902
                                                                                             2               10
                21         brave        1.59.120 (118.0.5993.88)  Ubuntu 22.04 xvfb          0            20912
                22         brave        1.60.114 (119.0.6045.124) Ubuntu 22.04 xvfb          0            20912

id        outcome_type outcome_value        test_name  test_status  \
36795  227596  <class 'NoneType'>          None  oac_window.open            2   
39814  230593  <class 'NoneType'>          None  oac_window.open            2   
39815  230594  <class 'NoneType'>          None       oac_iframe            2   

         test_message test_stack org_scheme                     org_host  \
36795  Test timed out       None       http  sub.headers.websec.saarland   
39814  Test timed out       None       http  sub.headers.websec.saarland   
39815  Test timed out       None       http  sub.headers.websec.saarland   

      resp_scheme  ... version headless_mode            os  automation_mode  \
36795       https  ...     119  headless-new  Ubuntu 22.04         selenium   
39814        http  ...     119          xvfb  Ubuntu 22.04         selenium   
39815       https  ...     119          xvfb  Ubuntu 22.04         selenium   

       add_info outcome_str  \
36795                  None   
39814                  None   
39815                  None   

                                               clean_url  \
36795  http://sub.headers.websec.saarland/_hp/tests/o...   
39814  http://sub.headers.websec.saarland/_hp/tests/o...   
39815  http://sub.headers.websec.saarland/_hp/tests/o...   

                                           browser  \
36795  edge Ubuntu 22.04 119 selenium headless-new   
39814          edge Ubuntu 22.04 119 selenium xvfb   
39815          edge Ubuntu 22.04 119 selenium xvfb   

                               org_origin                   resp_origin  
36795  http://sub.headers.websec.saarland  https://headers.webappsec.eu  
39814  http://sub.headers.websec.saarland   http://headers.webappsec.eu  
39815  http://sub.headers.websec.saarland  https://headers.webappsec.eu  

[3 rows x 34 columns]

In [259]:
display(df.loc[df["test_status"] == 2].groupby(["browser_id", "os", "test_name"])["id"].count().to_frame())

id
browser_id os           test_name            
4          Android 11   oac_iframe         45
                        oac_window.open     2
14         Ubuntu 22.04 referrer_iframe     1
15         Ubuntu 22.04 oac_window.open     1
                        referrer_iframe     1
19         Ubuntu 22.04 referrer_iframe     5
20         Ubuntu 22.04 oac_iframe          2
                        oac_window.open     3
                        referrer_iframe     5
23         Android 11   oac_iframe         58
                        oac_window.open     2
                        referrer_iframe    26
27         iPadOS 17.2  oac_iframe       3108
                        referrer_iframe  1736

In [260]:
# Time taken!
# NOTE: this is now broken as we ran all tests on linux twice for a stability analysis
df.groupby(["name", "version", "os", "headless_mode", "automation_mode", "org_scheme"])["created_at"].agg(["min", "max"]).apply(lambda x: x["max"] - x["min"], axis=1).to_frame()

0
name         version                   os           headless_mode automation_mode org_scheme                       
brave        1.59.120 (118.0.5993.88)  Ubuntu 22.04 headless-new  selenium        http       0 days 01:29:15.190542
                                                                                  https      0 days 01:26:48.371864
                                                    xvfb          selenium        http       0 days 01:30:28.246903
                                                                                  https      0 days 01:28:25.877146
             1.60.114 (119.0.6045.124) Ubuntu 22.04 headless-new  selenium        http       0 days 01:29:15.177088
                                                                                  https      0 days 01:26:53.931604
                                                    xvfb          selenium        http       0 days 01:30:25.268345
                                                                                  https      0 days 01:28:07.876485
             1.60.116                  Android 11   real          intent          http       0 days 02:18:48.616714
                                                                                  https      0 days 02:18:40.689261
             1.61 (23.12.18.22)        iPadOS 17.2  real          intent          http       0 days 19:28:40.622572
                                                                                  https      0 days 18:00:33.969640
chrome       119                       Ubuntu 22.04 headless-new  selenium        http       0 days 01:29:06.393217
                                                                                  https      0 days 01:26:43.887262
                                                    xvfb          selenium        http       0 days 01:30:11.077591
                                                                                  https      0 days 01:28:03.952745
             120.0.6099.119            iPadOS 17.2  real          intent          http       0 days 23:02:28.097676
                                                                                  https      0 days 01:26:58.776521
             120.0.6099.44             Android 11   real          intent          http       0 days 05:28:40.875672
                                                                                  https      0 days 05:28:32.296819
edge         119                       Ubuntu 22.04 headless-new  selenium        http       0 days 01:23:53.035976
                                                                                  https      0 days 01:27:01.534731
                                                    xvfb          selenium        http       0 days 01:24:54.645264
                                                                                  https      0 days 01:28:17.297944
             120.0.2210.116            iPadOS 17.2  real          intent          http       0 days 03:04:45.660061
                                                                                  https      0 days 01:26:03.106969
firefox      119                       Ubuntu 22.04 headless      selenium        http       0 days 01:25:19.112014
                                                                                  https      0 days 01:28:16.290569
                                                    xvfb          selenium        http       0 days 01:25:46.942611
                                                                                  https      0 days 01:27:57.987121
             121.0 (36782)             iPadOS 17.2  real          intent          http       1 days 02:50:28.319500
                                                                                  https      1 days 02:49:00.047567
firefox_beta 122.0b1                   Android 11   real          intent          http       0 days 05:39:01.169386
                                                      

## Response analysis

- We have 10456 unique tests: (test_name x relation_info) x org_scheme x (resp_scheme x resp_host) x response_id)

In [261]:
# Unique tests
tests = {
    "Fetch": [4, 2, 8, 6], 
    "Framing": [9, 2, 8, 35], # 7+11+17
    "PP": [4, 2, 8, 24],
    "OAC": [3, 2, 8, 14],
    "TAO": [1, 2, 8, 13],
    "RP": [2, 2, 8, 16],
    "CSP-SCRIPT": [2, 2, 8, 17],
    "COEP": [2, 2, 8, 11],
    "CORP": [4, 2, 8, 11],
    "CSP-IMG": [1, 2, 8, 17],
    "HSTS": [2, 1, 2, 14],
    "COOP": [1, 2, 8, 11],
}
tests = pd.DataFrame.from_dict(tests, columns=["tests", "org_origins", "resp_origins", "responses"], orient="index")
tests["All tests"] = tests.prod(axis=1)
tests.loc["Sum"] = tests.sum(axis=0)
tests

tests  org_origins  resp_origins  responses  All tests
Fetch           4            2             8          6        384
Framing         9            2             8         35       5040
PP              4            2             8         24       1536
OAC             3            2             8         14        672
TAO             1            2             8         13        208
RP              2            2             8         16        512
CSP-SCRIPT      2            2             8         17        544
COEP            2            2             8         11        352
CORP            4            2             8         11        704
CSP-IMG         1            2             8         17        272
HSTS            2            1             2         14         56
COOP            1            2             8         11        176
Sum            35           23            90        189      10456

In [262]:
# Only consider the tests that did not timeout! (we already reran them above)
df_org = df
df = df.loc[df["test_status"] == 0]

In [263]:
# SELECT count(*) as c2, count(DISTINCT browser_id), count(DISTINCT outcome_value) as c1, test_name, org_scheme, org_host, resp_scheme, resp_host, relation_info, response_id 
# FROM "Result" GROUP by test_name, org_scheme, org_host, resp_scheme, resp_host, relation_info, response_id order by c1 DESC, c2 DESC

res = df.groupby(["test_name", "org_scheme", "org_host", "resp_scheme", "resp_host", "relation_info", "response_id"])[["browser_id", "outcome_str"]].agg(["count", "nunique"])
display(res)
display(res.value_counts().to_frame())

browser_id  \
                                                                                                                                    count   
test_name             org_scheme org_host                    resp_scheme resp_host                   relation_info response_id              
accesswindow_direct   http       sub.headers.websec.saarland http        headers.webappsec.eu        direct        71                  38   
                                                                                                                   72                  40   
                                                                                                                   73                  39   
                                                                                                                   74                  38   
                                                                                                                   75                  38   
...                                                                                                                                   ...   
upgradeHSTS_subdomain http       sub.headers.websec.saarland https       sub.headers.websec.saarland subdomain     139                 38   
                                                                                                                   140                 38   
                                                                                                                   141                 38   
                                                                                                                   142                 38   
                                                                                                                   143                 38   

                                                                                                                                        \
                                                                                                                               nunique   
test_name             org_scheme org_host                    resp_scheme resp_host                   relation_info response_id           
accesswindow_direct   http       sub.headers.websec.saarland http        headers.webappsec.eu        direct        71               19   
                                                                                                                   72               19   
                                                                                                                   73               19   
                                                                                                                   74               19   
                                                                                                                   75               19   
...                                                                                                                                ...   
upgradeHSTS_subdomain http       sub.headers.websec.saarland https       sub.headers.websec.saarland subdomain     139              19   
                                                                                                                   140              19   
                                                                                                                   141              19   
                                                                                                                   142              19   
                                                                                                                   143              19   

                                                                                                                               outcome_str  \
                                                                             

count
(browser_id, count) (browser_id, nunique) (outcome_str, count) (outcome_str, nunique)       
39                  19                    39                   1                        2343
40                  19                    40                   1                        1307
43                  19                    43                   1                         886
42                  19                    42                   1                         652
41                  19                    41                   1                         524
...                                                                                      ...
53                  19                    53                   4                           1
54                  19                    54                   3                           1
55                  19                    55                   4                           1
                                                               3                           1
64                  18                    64                   1                           1

[118 rows x 1 columns]

## Stability analysis
- Does the same browser/env always result in the same outcomes?
- We ran all tests on linux twice, does any of these tests have more than one result?
    - A total of 20/10456 tests have different outcomes
    - ~~2xreferrer_iframe (both timeout of the test "None" vs "message timeout" result); can be fixed by removing timeouts first~~
    - 18x subresourceloadingCOEP_img, all differences: 'swag-same-origin.jpg': 'error' | 'load'
        - trying to manually reproduce: e.g., http://sub.headers.websec.saarland/_hp/tests/subresource-loading-coep.sub.html?resp_type=basic&browser_id=1&label=COEP&first_id=57&last_id=57&scheme=http
        - devtools open: with cache disabeled: 15x error, without cache disabled: 13x or 16x error?
        - devtools closed: 13x or 16x error (tried to fix with Cache-Control: no-cache, no-store but does not seem to have an effect)
        - chrome always 14x error
    - 13x firefox xvfb, 6x firefox headless, 1x edge

In [264]:
stab = df.groupby(["test_name", "org_scheme", "org_host", "resp_scheme", "resp_host", "relation_info", "response_id", "browser_id"])[["outcome_str"]].agg(["count", "nunique"])
# Tests with more than one outcome
diff_outcomes = stab.loc[stab[("outcome_str", "nunique")] != 1]
print(f"{len(diff_outcomes)} tests have different outcomes!")
display(diff_outcomes.reset_index()["browser_id"].apply(id_to_browser).value_counts().to_frame())
display(diff_outcomes)

1063 tests have different outcomes!


count
browser_id                                             
firefox iPadOS 17.2 121.0 (36782) intent real       792
operagx iPadOS 17.2 2.2.2 intent real               162
firefox_beta Android 11 122.0b1 intent real          47
brave Android 11 1.60.116 intent real                22
firefox Ubuntu 22.04 119 selenium headless           18
firefox Ubuntu 22.04 119 selenium xvfb               12
edge iPadOS 17.2 120.0.2210.116 intent real           5
brave iPadOS 17.2 1.61 (23.12.18.22) intent real      3
chrome Android 11 120.0.6099.44 intent real           2

outcome_str  \
                                                                                                                                                         count   
test_name                  org_scheme org_host                    resp_scheme resp_host                       relation_info response_id browser_id               
accesswindow_direct        http       sub.headers.websec.saarland http        headers.websec.saarland         direct        72          3                    3   
                                                                                                                            80          3                    2   
fullscreen_iframe          http       sub.headers.websec.saarland http        headers.webappsec.eu            child         162         29                   4   
                                                                                                                            163         29                   4   
                                                                                                                            164         29                   4   
...                                                                                                                                                        ...   
subresourceloadingCOEP_img https      sub.headers.websec.saarland https       sub.headers.websec.saarland     direct        64          23                   2   
                                                                              sub.sub.headers.websec.saarland direct        58          14                   2   
                                                                                                                                        23                   2   
                                                                                                                            62          23                   2   
                                                                                                                            64          23                   2   

                                                                                                                                                            
                                                                                                                                                   nunique  
test_name                  org_scheme org_host                    resp_scheme resp_host                       relation_info response_id browser_id          
accesswindow_direct        http       sub.headers.websec.saarland http        headers.websec.saarland         direct        72          3                2  
                                                                                                                            80          3                2  
fullscreen_iframe          http       sub.headers.websec.saarland http        headers.webappsec.eu            child         162         29               2  
                                                                                                                            163         29               2  
                                                                                                                            164         29               2  
...                                                                                                                                                    ...  
subresourceloadingCOEP_img https      sub.headers.websec.saarland https       sub.headers.websec.saarland     direct        64          23               2  
                                                                              sub.sub.headers.websec.saarland direct        58          14               2  
                                                                                                                                        23             

In [266]:
for test_name, org_scheme, org_host, resp_scheme, resp_host, relation_info, response_id, browser_id in stab.loc[stab[("outcome_str", "nunique")] != 1].index:
    print(test_name)
    rows = df.loc[(df["org_scheme"] == org_scheme) & (df["test_name"] == test_name) & (df["resp_scheme"] == resp_scheme) & (df["resp_host"] == resp_host) & (df["relation_info"] == relation_info) & (df["response_id"] == response_id) & (df["browser_id"] == browser_id)]
    with pd.option_context("display.max_colwidth", 200):
        #display(rows[["outcome_str", "name", "headless_mode", "os", "version"]].value_counts().to_frame())
        display(rows[["outcome_str", "name"]].value_counts().to_frame())
        disp = rows.drop_duplicates(subset="outcome_str")[["browser_id", "os", "headless_mode", "name", "outcome_str", "raw_header", "test_name", "org_scheme", "org_host", "resp_scheme", "relation_info", "resp_host", "full_url"]]
        disp = disp.style.format({'full_url': make_clickable})
        display(disp)
        

accesswindow_direct


count
outcome_str                                        name        
{'window.open.opener': 'null'}                     brave      2
{'window.open.opener': 'object "[object Window]"'} brave      1

accesswindow_direct


count
outcome_str                                        name        
{'window.open.opener': 'null'}                     brave      1
{'window.open.opener': 'object "[object Window]"'} brave      1

fullscreen_iframe


...

count
outcome_str                                                                                                                                                               name               
{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'load', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'error'}, 'window.crossOriginIsolated': False} firefox_beta      1
{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'load', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'load'}, 'window.crossOriginIsolated': False}  firefox_beta      1

subresourceloadingCOEP_img


count
outcome_str                                                                                                                                                               name               
{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'load', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'error'}, 'window.crossOriginIsolated': False} firefox_beta      1
{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'load', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'load'}, 'window.crossOriginIsolated': False}  firefox_beta      1

subresourceloadingCOEP_img


count
outcome_str                                                                                                                                                                name               
{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'error', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'error'}, 'window.crossOriginIsolated': False} firefox_beta      1
{'image-events': {'swag.jpg': 'load', 'swag-same-site.jpg': 'load', 'swag-cross-site.jpg': 'load', 'swag-same-origin.jpg': 'load'}, 'window.crossOriginIsolated': False}   firefox_beta      1

## Differences:
- COOP (accesswindow_direct):
    - [ ] Edge + Firefox: redirect first
    - [ ] Brave + Chrome: COOP first?
-  Framing:
    -  [ ] framing_iframe_sandbox: CSP-FA *; Firefox allows, all other browsers deny?
- PP not supported in Firefox
- OAC not supported in Firefox
    - [ ] Also random/caching behavior?
- PerfAPI:
    - [ ] Chrome/Firefox have different rules when to create an entry at all?
- COEP (CORP):
    - [ ] Firefox incorrect behavior for same-origin (applies same-site?)
- CORP:
    - [ ] same-origin: Edge does not check the scheme?
    - [x] Firefox applies CORP on object tags (even though it should not!)
    - [ ] Some other CORP and/or COEP strange stuff (Firefox)
- Referrer Policy: different default in Brave (unsafe-url is never allowed)
- Subresource-loading (CSP): differences due to HTTPS Upgrades
- Script Execution (CSP):
    - [ ] Safari sandbox bug?! (maybe related https://bugs.webkit.org/show_bug.cgi?id=223848 unsure though)
- Upgrade (HSTS):
    - [ ] Safari bug?

In [267]:
def get_uniques(df):
    browsers = f"{df['name'].unique().tolist()}"
    try:
        outcome = unique_outcomes[df.name[0]]
    except KeyError:
        outcome = {}
        #outcome = []
    outcome[browsers] = df.name[1]
    #outcome.append(f"{df.name[1]} ({browsers})")
    unique_outcomes[df.name[0]] = outcome

for grouping, group in df.groupby(["test_name", "relation_info"]):
    
    unique_outcomes = {}
    group.groupby(["name"])["outcome_str"].value_counts(normalize=True).reset_index().groupby(["outcome_str", "proportion"], group_keys=True).apply(get_uniques)
    d = pd.DataFrame.from_dict(unique_outcomes, orient="index")
    if d.shape[1] != 1:
        print(grouping)
        # display(unique_outcomes)
        display(group.groupby(["name"])["outcome_str"].value_counts(normalize=True).to_frame().unstack(0))
        for value, dic in unique_outcomes.items():
            values = [f"{v} ({k})" for k,v in dic.items()]
            # print(f"{value}: {values}")
        display(d)
        print()


('accesswindow_direct', 'direct')


proportion            \
name                                                    brave    chrome   
outcome_str                                                               
{'window.open.opener': 'null'}                       0.267784  0.301966   
{'window.open.opener': 'object "TypeError: Cann...        NaN       NaN   
{'window.open.opener': 'object "TypeError: null...   0.198913       NaN   
{'window.open.opener': 'object "[object Window]"'}   0.533303  0.698034   

                                                                        \
name                                                    edge   firefox   
outcome_str                                                              
{'window.open.opener': 'null'}                      0.181818  0.182983   
{'window.open.opener': 'object "TypeError: Cann...       NaN       NaN   
{'window.open.opener': 'object "TypeError: null...       NaN       NaN   
{'window.open.opener': 'object "[object Window]"'}  0.818182  0.817017   

                                                                           \
name                                               firefox_beta     opera   
outcome_str                                                                 
{'window.open.opener': 'null'}                         0.183673  0.181818   
{'window.open.opener': 'object "TypeError: Cann...          NaN       NaN   
{'window.open.opener': 'object "TypeError: null...          NaN       NaN   
{'window.open.opener': 'object "[object Window]"'}     0.816327  0.818182   

                                                                       
name                                                 operagx ucmobile  
outcome_str                                                            
{'window.open.opener': 'null'}                      0.181818      NaN  
{'window.open.opener': 'object "TypeError: Cann...       NaN      1.0  
{'window.open.opener': 'object "TypeError: null...       NaN      NaN  
{'window.open.opener': 'object "[object Window]"'}  0.818182      NaN

['edge', 'opera', 'operagx']  \
{'window.open.opener': 'null'}                                          0.181818   
{'window.open.opener': 'object "[object Window]"'}                      0.818182   
{'window.open.opener': 'object "TypeError: null...                           NaN   
{'window.open.opener': 'object "TypeError: Cann...                           NaN   

                                                    ['firefox']  \
{'window.open.opener': 'null'}                         0.182983   
{'window.open.opener': 'object "[object Window]"'}     0.817017   
{'window.open.opener': 'object "TypeError: null...          NaN   
{'window.open.opener': 'object "TypeError: Cann...          NaN   

                                                    ['firefox_beta']  \
{'window.open.opener': 'null'}                              0.183673   
{'window.open.opener': 'object "[object Window]"'}          0.816327   
{'window.open.opener': 'object "TypeError: null...               NaN   
{'window.open.opener': 'object "TypeError: Cann...               NaN   

                                                    ['brave']  ['chrome']  \
{'window.open.opener': 'null'}                       0.267784    0.301966   
{'window.open.opener': 'object "[object Window]"'}   0.533303    0.698034   
{'window.open.opener': 'object "TypeError: null...   0.198913         NaN   
{'window.open.opener': 'object "TypeError: Cann...        NaN         NaN   

                                                    ['ucmobile']  
{'window.open.opener': 'null'}                               NaN  
{'window.open.opener': 'object "[object Window]"'}           NaN  
{'window.open.opener': 'object "TypeError: null...           NaN  
{'window.open.opener': 'object "TypeError: Cann...           1.0


('fetch_GET', 'credentials')


proportion            \
name                                                    brave    chrome   
outcome_str                                                               
{'error': 'null', 'headers': 'access-control-al...   0.023343  0.020619   
{'error': 'null', 'headers': 'access-control-al...   0.021084  0.020619   
{'error': 'null', 'headers': 'access-control-al...   0.020331  0.020619   
{'error': 'null', 'headers': 'access-control-al...   0.019578  0.021907   
{'error': 'null', 'headers': 'access-control-al...   0.021084  0.020619   
{'error': 'null', 'headers': 'content-length,te...   0.031627  0.030928   
{'error': 'object "TypeError: Failed to fetch"'...   0.862952  0.864691   

                                                                        \
name                                                    edge   firefox   
outcome_str                                                              
{'error': 'null', 'headers': 'access-control-al...  0.021605  0.021382   
{'error': 'null', 'headers': 'access-control-al...  0.021605  0.021382   
{'error': 'null', 'headers': 'access-control-al...  0.021605  0.019737   
{'error': 'null', 'headers': 'access-control-al...  0.018519  0.023026   
{'error': 'null', 'headers': 'access-control-al...  0.020062  0.023026   
{'error': 'null', 'headers': 'content-length,te...  0.027778  0.034539   
{'error': 'object "TypeError: Failed to fetch"'...  0.868827  0.856908   

                                                                           \
name                                               firefox_beta     opera   
outcome_str                                                                 
{'error': 'null', 'headers': 'access-control-al...     0.020833  0.015625   
{'error': 'null', 'headers': 'access-control-al...     0.020833  0.015625   
{'error': 'null', 'headers': 'access-control-al...     0.020833  0.027344   
{'error': 'null', 'headers': 'access-control-al...     0.020833  0.015625   
{'error': 'null', 'headers': 'access-control-al...     0.020833  0.035156   
{'error': 'null', 'headers': 'content-length,te...     0.031250  0.023438   
{'error': 'object "TypeError: Failed to fetch"'...     0.864583  0.867188   

                                                                              
name                                                 operagx safari ucmobile  
outcome_str                                                                   
{'error': 'null', 'headers': 'access-control-al...  0.020270    NaN      NaN  
{'error': 'null', 'headers': 'access-control-al...  0.023649    NaN  0.03125  
{'error': 'null', 'headers': 'access-control-al...  0.020270    NaN  0.03125  
{'error': 'null', 'headers': 'access-control-al...  0.013514    NaN      NaN  
{'error': 'null', 'headers': 'access-control-al...  0.020270  0.125  0.06250  
{'error': 'null', 'headers': 'content-length,te...  0.020270    NaN      NaN  
{'error': 'object "TypeError: Failed to fetch"'...  0.881757  0.875  0.87500

...

proportion                                \
name                                brave    chrome      edge   firefox   
outcome_str                                                               
{'response.redirected': False}   0.814208  0.814159  0.809524  0.819444   
{'response.redirected': True}    0.185792  0.185841  0.190476  0.180556   

                                                                 
name                           firefox_beta     opera   operagx  
outcome_str                                                      
{'response.redirected': False}     0.821429  0.821429  0.785714  
{'response.redirected': True}      0.178571  0.178571  0.214286

['operagx']  ['edge']  ['chrome']  ['brave']  \
{'response.redirected': False}     0.785714  0.809524    0.814159   0.814208   
{'response.redirected': True}      0.214286  0.190476    0.185841   0.185792   

                                ['firefox']  ['firefox_beta', 'opera']  
{'response.redirected': False}     0.819444                   0.821429  
{'response.redirected': True}      0.180556                   0.178571


('upgradeHSTS_subdomain', 'subdomain')


proportion                                \
name                                brave    chrome      edge   firefox   
outcome_str                                                               
{'response.redirected': False}   0.893443  0.893805  0.892857  0.895833   
{'response.redirected': True}    0.106557  0.106195  0.107143  0.104167   

                                                                 
name                           firefox_beta     opera   operagx  
outcome_str                                                      
{'response.redirected': False}     0.892857  0.892857  0.892857  
{'response.redirected': True}      0.107143  0.107143  0.107143

['edge', 'firefox_beta', 'opera', 'operagx']  \
{'response.redirected': False}                                      0.892857   
{'response.redirected': True}                                       0.107143   

                                ['brave']  ['chrome']  ['firefox']  
{'response.redirected': False}   0.893443    0.893805     0.895833  
{'response.redirected': True}    0.106557    0.106195     0.104167

In [268]:
test_name_seen = set()
for test_name, org_scheme, org_host, resp_scheme, resp_host, relation_info, response_id in res.loc[res[("outcome_str", "nunique")] != 1].index:
    # Only look at each feature group once
    if test_name in test_name_seen:
        continue
    test_name_seen.add(test_name)
    print(test_name)
    rows = df.loc[(df["org_scheme"] == org_scheme) & (df["test_name"] == test_name) & (df["resp_scheme"] == resp_scheme) & (df["resp_host"] == resp_host) & (df["relation_info"] == relation_info) & (df["response_id"] == response_id)]
    with pd.option_context("display.max_colwidth", 200):
        #display(rows[["outcome_str", "name", "headless_mode", "os", "version"]].value_counts().to_frame())
        display(rows[["outcome_str", "name"]].value_counts().to_frame())
        disp = rows.drop_duplicates(subset="outcome_str")[["browser_id", "headless_mode", "name", "outcome_str", "raw_header", "test_name", "org_scheme", "org_host", "resp_scheme", "relation_info", "resp_host", "full_url"]]
        disp = disp.style.format({'full_url': make_clickable})
        display(disp)
        
    

accesswindow_direct


count
outcome_str                                                                                   name               
{'window.open.opener': 'object "[object Window]"'}                                            brave            10
                                                                                              chrome            8
                                                                                              edge              6
                                                                                              firefox           5
{'window.open.opener': 'object "TypeError: null is not an object (evaluating \'w.opener\')"'} brave             3
{'window.open.opener': 'object "[object Window]"'}                                            firefox_beta      2
                                                                                              opera             2
                                                                                              operagx           2

framing_embed


count
outcome_str     name               
message send    brave            10
                chrome            5
                edge              4
                firefox           4
message timeout operagx           4
                chrome            3
                brave             3
                edge              3
message send    firefox_beta      2
                opera             2
message timeout firefox           2

framing_iframe


...

count
outcome_str name               
load        brave            10
            chrome            8
error       firefox           7
load        edge              6
error       operagx           2
            firefox_beta      2
            brave             2
load        opera             2

subresourceloadingCORP_object


count
outcome_str             name               
load                    brave            10
                        chrome            6
                        edge              4
                        firefox           4
timeout: no event fired brave             3
load                    firefox_beta      2
                        opera             2
timeout: no event fired chrome            2
                        edge              2
                        firefox           2
                        operagx           2

upgradeHSTS_direct


count
outcome_str                    name               
{'response.redirected': False} brave            10
                               chrome            6
                               edge              4
                               firefox           4
{'response.redirected': True}  brave             3
{'response.redirected': False} firefox_beta      2
                               opera             2
{'response.redirected': True}  chrome            2
                               edge              2
                               operagx           2
                               firefox           1

## Clustering and co.
- Maybe try decision trees again?
- One tree for each feature group?/label?/test_name?
    - outcome = outcome_str (mostly binary, sometimes more options)
    - variables:
        - browser (includes os, automation mode, headless mode, version)
        - test_id = test_name + relation_info (or only relation_info if one tree per test_name is created)
        - org_orgin = org_scheme + org_host
        - resp_origin = resp_scheme + resp_host
        - response_id or raw_headers + status_code
        - ...
     
- H2O setup:
    - `sudo apt install openjdk-17-jre-headless graphviz`
    - `wget https://h2o-release.s3.amazonaws.com/h2o/rel-3.44.0/2/h2o-3.44.0.2.zip`
    - `unzip h2o-3.44.0.2.zip`
    - `cd h2o-3.44.0.2` and `java -jar h2o.jar`

In [269]:
df[["test_name", "label", "relation_info"]].value_counts()

test_name                      label       relation_info 
fullscreen_iframe              PP          child_allow       16168
                                           child             16168
                                           direct            16168
                                           child_sandbox     16168
referrer_iframe                RP          iframe            11303
framing_iframe                 CSP-FA      sandbox           11192
framing_object                 CSP-FA      sandbox           11192
                                           nested            11192
framing_iframe                 CSP-FA      nested            11192
                                           direct            11192
framing_embed                  CSP-FA      sandbox           11192
                                           nested            11192
                                           direct            11192
framing_object                 CSP-FA      direct            11192
refe

In [281]:
h2o.init(nthreads=50, max_mem_size="100G", log_level="WARN")
h2o.no_progress()


# Only keep one row for each test
# If the test had non-deterministic results, chose the first? (this should only be Firefox COEP same-origin 18x in desktop + some mobile results)
print("Original data entries", len(df))
tree_df = df.drop_duplicates(subset=["test_name", "relation_info", "browser", "org_origin", "resp_origin", "response_id"])
print("Only one row for each test (per browser)", len(tree_df))

# Remove browsers that currently do not have almost all results
tree_df = tree_df.loc[~tree_df["browser_id"].isin([4, 28, 30])]
print("Remove failed browsers", len(tree_df))

# Idea limit on responses that have more than one outcome!
# This will remove all the branches that are the same in all browsers (and make trees large and confusing)
condition = tree_df.groupby(["test_name", "org_scheme", "org_host", "resp_scheme", "resp_host", "relation_info", "response_id"])["outcome_str"].transform("nunique") != 1
tree_df = tree_df.loc[condition]
print("Remove tests that are the same in all browsers", len(tree_df))

base_dir = f"trees/{datetime.today().strftime('%Y-%m-%dT%H:%M')}" 

for group_name, group in tree_df.groupby(["test_name", "relation_info"]):
    print(group_name)
    # pred_cols = ["browser", "relation_info", "org_origin", "resp_origin", "status_code", "raw_header"]
    pred_cols = ["browser", "org_origin", "resp_origin", "status_code", "raw_header"]

    group = group[["outcome_str", *pred_cols]]
    # Convert all columns to str, then to category
    tree = make_tree(group, pred_cols, group_name, base_dir)
    # print(tree)


Checking whether there is an H2O instance running at http://localhost:54321. connected.


--------------------------  -----------------------------
H2O_cluster_uptime:         18 days 3 hours 34 mins
H2O_cluster_timezone:       Etc/UTC
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.44.0.2
H2O_cluster_version_age:    2 months
H2O_cluster_name:           H2O_from_python_ubuntu_uy37br
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    99.8 Gb
H2O_cluster_total_cores:    160
H2O_cluster_allowed_cores:  50
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://localhost:54321
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.11.5 final
--------------------------  -----------------------------

Original data entries 429909
Only one row for each test (per browser) 198357
Remove failed browsers 198074
Remove tests that are the same in all browsers 55247
('accesswindow_direct', 'direct')
Connecting to H2O server at http://localhost:54321 ... successful.


--------------------------  -----------------------------
H2O_cluster_uptime:         18 days 3 hours 34 mins
H2O_cluster_timezone:       Etc/UTC
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.44.0.2
H2O_cluster_version_age:    2 months
H2O_cluster_name:           H2O_from_python_ubuntu_uy37br
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    99.8 Gb
H2O_cluster_total_cores:    160
H2O_cluster_allowed_cores:  50
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://localhost:54321
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.11.5 final
--------------------------  -----------------------------

Create tree: ('accesswindow_direct', 'direct'), datapoints: 3343
('framing_embed', 'direct')
Connecting to H2O server at http://localhost:54321 ... successful.


...

Create tree: ('subresourceloadingCORP_img', 'direct'), datapoints: 19
('subresourceloadingCORP_object', 'direct')
Connecting to H2O server at http://localhost:54321 ... successful.


--------------------------  -----------------------------
H2O_cluster_uptime:         18 days 3 hours 34 mins
H2O_cluster_timezone:       Etc/UTC
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.44.0.2
H2O_cluster_version_age:    2 months
H2O_cluster_name:           H2O_from_python_ubuntu_uy37br
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    99.8 Gb
H2O_cluster_total_cores:    160
H2O_cluster_allowed_cores:  50
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://localhost:54321
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.11.5 final
--------------------------  -----------------------------

Create tree: ('subresourceloadingCORP_object', 'direct'), datapoints: 3336
('upgradeHSTS_direct', 'direct')
Connecting to H2O server at http://localhost:54321 ... successful.


--------------------------  -----------------------------
H2O_cluster_uptime:         18 days 3 hours 34 mins
H2O_cluster_timezone:       Etc/UTC
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.44.0.2
H2O_cluster_version_age:    2 months
H2O_cluster_name:           H2O_from_python_ubuntu_uy37br
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    99.8 Gb
H2O_cluster_total_cores:    160
H2O_cluster_allowed_cores:  50
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://localhost:54321
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.11.5 final
--------------------------  -----------------------------

Create tree: ('upgradeHSTS_direct', 'direct'), datapoints: 19


# Crash analysis OLD

### Exceptions thrown
- Fixed:
    - Only Firefox; both headless + Xvfb
        - OAC + RP
        - Both on HTTP and HTTPS
        - Response_ids: 185, 186, 341, 342; these are the ones that have status code 302!
        - Reason seems to be that Firefox switches to another tab in these cases and thus the wait for crashes. Solution: forcefully switch back to the original tab before waiting!
    - Only Brave: both headless + Xvfb
        - OAC + RP
        - Both on HTTP and HTTPS
        - Reason seems to be the tab switching, if deactivated no issue occurs

In [165]:
with open("/home/ubuntu/wpt/_hp/tools/crawler/desktop-selenium-2023-11-20 16:09:24.649008.log", "r") as f:
    crashes = []
    for l in f.readlines():
        if "649008: http" in l:
            match = re.match(".*(http|https)://.*browser_id=(\d+)&label=(.*)&first_id=(\d+).*", l)
            crashes.append([match[1], match[2], match[3], match[4]])

In [166]:
crashes = pd.DataFrame(crashes, columns=["scheme", "browser_id", "label", "response_id"]).drop_duplicates()
crashes

scheme browser_id label response_id
0    http         59    RP         172
2    http         59    RP         173
4   https         59   OAC         339
6   https         59    RP         181
8    http         75    RP         171
10   http         75    RP         172
12  https         75   OAC         330
14  https         75   OAC         338
16  https         75    RP         180
18  https         74   OAC         337
20  https         74    RP         175